In [ ]:
from soundtrack import *
import time
import sqlite3
from IPython.display import clear_output
import IPython
from datetime import datetime, timedelta
import pickle
import datetime as dt

db_name=db_name()
buffer_sleep=0 #adjust if laggy connection to prevent STs from get skipped.
filename='music_dict.p' #purpose is to have smartshuffle list ready so to not wait and rotate in new songs 4x/daily
try:
    music_dict=music_dict
    print("*******No pickle needed*********") #it is preferable to have music_dict list because this will have removals
except:
    print("*******Pickle needed*********")
    music_dict=pickle.load(open(filename,"rb")) #use pickle if there is no smartshuffle list available already
while datetime.now().hour < 24: #not sure if ever false for more than one second per day. redo 20190807  
    for song in music_dict:
        b=song[1][2]
        current_datetime=datetime.now().strftime('%A %H:%M:%S')
        #b=float(getMediaDuration(song[0]))
        con = sqlite3.connect(db_name)
        print("Current Time:{}".format(current_datetime))
        table='song_schedule'
        current_dow=datetime.now().strftime('%w')
        current_time=datetime.now().strftime('%H:%M:%S')
        statement="SELECT * FROM {} WHERE dow='{}' AND time >'{}' ORDER BY dow ASC, time ASC LIMIT 0,1".format(table,current_dow,current_time)
        cursor=con.execute(statement)
        rows = cursor.fetchall()
        for row in rows:
            #print(row)
            next_song_time=datetime.strptime(row[1],'%H:%M:%S').time()
        song_dt = dt.datetime.combine(dt.date.today(), next_song_time)
        now=dt.datetime.now()
        difference=song_dt-now
        difference=difference.seconds
        print("{} seconds until next Soundtrack song.".format(difference))
        end_tm=datetime.now() + timedelta(0,float(3000))
        end_tm=end_tm.strftime('%H:%M:%S')
        beg_tm=datetime.now() + timedelta(0,float(-3000))
        beg_tm=beg_tm.strftime('%H:%M:%S')
        statement="SELECT * FROM {} WHERE dow={} ORDER BY dow ASC, time ASC".format(table,current_dow)
        cursor=con.execute(statement)
        rows = cursor.fetchall()
        i=0
        for row2 in rows:
            if str(beg_tm) < row2[1] < str(end_tm):
                #print a few st songs before and after now
                if ((str(current_time) < row2[1]) and i==0):
                    print("Next: {}".format(row2[0:3]))
                    i=i+1
                else:
                    print(row2[0:3])
        #time algos
        if difference < 60: #play ST song
            print("Less than 60 seconds") 
            #1 - 30 sec silence before a scheduled song is fine, seems Pavlovian on the long end.
            time.sleep(difference/2) #play early, but wait half the time. 
            music_folder='/home/pi/Music/'
            song=music_folder+row[2]
            b=float(getMediaDuration(song))
            print("{} is {} seconds.".format(song,b))
            IPython.display.display(IPython.display.Audio(song,autoplay=True, embed=None))            
            time.sleep(b+buffer_sleep+2) #an additional 2 seconds for STs to play until the end
            #clear_output()
            break
        elif difference < 300: #find a shuffle song that fits this short gap before next ST
            if 1 < difference-b <= 15:
                music_dict.remove(song) #remove shuffle song about to play so that next time start program it skips
                IPython.display.display(IPython.display.Audio(song[0],autoplay=True, embed=None))
                print("Now Playing(pre-ST): {} : {} seconds : ".format(getMediaName(song[0]),b), end="")
                next_tm = datetime.now() + timedelta(0,float(b))
                print("Ends @ {}".format(next_tm.time()))
                statement=getShuffleCountExists(song[0])
                incrementShuffleCount(statement,song)
                time.sleep(b+buffer_sleep)
                break
        elif b < difference: #play shuffle song  
            music_dict.remove(song)
            IPython.display.display(IPython.display.Audio(song[0],autoplay=True, embed=None))
            print("Now Playing: {} : {} seconds : ".format(getMediaName(song[0]),b), end="")
            next_tm = datetime.now() + timedelta(0,float(b))
            print("Ends @ {}".format(next_tm.time()))
            statement=getShuffleCountExists(song[0])
            incrementShuffleCount(statement,song)
            time.sleep(b+buffer_sleep)
        clear_output()

*******Pickle needed*********
Current Time:Thursday 19:30:58
841 seconds until next Soundtrack song.
(4, '18:45:00', 'Ride-LeaveThemAllBehind.mp3')
(4, '19:00:00', 'TheBreeders-Cannonball.mp3')
(4, '19:07:30', 'shuffle_exclude/Snow_Patrol_-_Called_Out_In_The_Dark.mp3')
(4, '19:15:00', 'Big_Audio_Dynamite_-_The_Bottom_Line.mp3')
(4, '19:30:00', 'outkast-hey_ya.mp3')
Next: (4, '19:45:00', 'morphine-telegram.mp3')
(4, '20:00:00', 'Belle_and_sebastian-TheBoyWithTheArabStrap.mp3')
(4, '20:15:00', 'shuffle_exclude/Fine_Young_Cannibals-She_Drives_Me_Crazy.mp3')


Now Playing: gerald_neale-absolution.mp3 : 145 seconds : Ends @ 19:33:23.755218
UPDATE shuffle_count SET cnt=28,time="2019-08-08 19:30:58" WHERE name="/home/pi/Music/gerald_neale-absolution.mp3"


In [2]:
print(music_dict)

[('/home/pi/Music/ATribeCalledQuest-CanIKickIt.mp3', (20, 1, 260)), ('/home/pi/Music/BronskiBeat-SmalltownBoy.mp3', (20, 2, 298)), ('/home/pi/Music/Snow_Patrol_-_You_re_All_I_Have.mp3', (20, 3, 229)), ('/home/pi/Music/duran_duran-perfect_day.mp3', (20, 4, 227)), ('/home/pi/Music/Pearl_Jam-_Immortality_W_Lyrics.mp3', (20, 10, 301)), ('/home/pi/Music/air___10.mp3', (20, 12, 265)), ('/home/pi/Music/My_Darling.mp3', (20, 13, 218)), ('/home/pi/Music/TheMagicNumbers-LoveIsJustAGame.mp3', (20, 17, 293)), ('/home/pi/Music/AFlockOfSeagulls-SpaceAgeLoveSong.mp3', (20, 18, 227)), ('/home/pi/Music/Imogen Heap - Headlock.mp3', (20, 20, 207)), ('/home/pi/Music/Natalie_Merchant_Carnival.mp3', (20, 27, 359)), ('/home/pi/Music/Coldplay_-_Magic_Official_Video.mp3', (20, 29, 316)), ('/home/pi/Music/09 The Upsetter.mp3', (20, 30, 230)), ('/home/pi/Music/Tom_Petty_-_Yer_So_Bad_Official_Music_Video.mp3', (20, 36, 218)), ('/home/pi/Music/Matthew_Sweet_-_Girlfriend.mp3', (20, 37, 223)), ('/home/pi/Music/duran